In [9]:
import numpy as np
from scipy.integrate import odeint
from tqdm import tqdm
import time
from deap import base, creator, tools, algorithms
import random

# Constants
a21 = 1
a31 = 0.27
a32 = 0.73

a41 = 0.18
a42 = 0.24
a43 = 0.58

a51 = 0.24
a52 = 0.23
a53 = 0.2
a54 = 0.33

W2 = 63000
W3 = 20000
W4 = 15000
W5 = 33000
Ws2 = 8000

#P980 = 3*10**4  # our PD



def system(state, t, x, P980, c1, c2, c3, c4, k31, k41, k51):

    ns2, n1, n2, n3, n4, n5 = state

    #ns2
    ms2 = 1.23*P980*(37*(100-x)-ns2) - Ws2*ns2 - (c1*n1+c2*n2+c3*n3+c4*n4)*ns2  # ns1 = total_Yb - ns2

    # n1
    m1 = -c1*n1*ns2 + a21*W2*n2 + a31*W3*n3 + a41*W4*n4 + a51*W5*n5 - k41*n1*n4 - k31*n1*n3 - k51*n5*n1

    # n2
    m2 = c1*n1*ns2 - c2*n2*ns2 - a21*W2*n2 + a32*W3*n3 + a42*W4*n4 + a52*W5*n5 + k41*n1*n4 + 2*k31*n1*n3

    # n3
    m3 = c2*n2*ns2 - c3*n3*ns2 - (a31+a32)*W3*n3 + a43*W4*n4 + a53*W5*n5 + 2*k51*n1*n5 + k41*n1*n4 - k31*n1*n3

    # n4
    m4 = c3*n3*ns2 - c4*n4*ns2 - (a43+a42+a41)*W4*n4 + a54*W5*n5 - k41*n1*n4

    # n5
    m5 = c4*n4*ns2 - (a54+a53+a52+a51)*W5*n5 - k51*n1*n5


    return [ms2, m1, m2, m3, m4, m5]


In [10]:
P980_values = [1.2*10**3, 1.8*10**3, 2.8*10**3, 4.4*10**3, 5*10**3, 6*10**3, 7.5*10**3, 9.1*10**3, 1.1*10**4, 1.4*10**4, 1.7*10**4, 2*10**4, 2.3*10**4, 2.7*10**4, 3*10**4]

P980_values8 = [1.8*10**3, 2.8*10**3, 4.4*10**3, 5*10**3, 6*10**3, 7.5*10**3, 9.1*10**3, 1.1*10**4, 1.4*10**4, 1.7*10**4, 2*10**4, 2.3*10**4, 2.7*10**4, 3*10**4]

P980_values10 = [2.8*10**3, 4.4*10**3, 5*10**3, 6*10**3, 7.5*10**3, 9.1*10**3, 1.1*10**4, 1.4*10**4, 1.7*10**4, 2*10**4, 2.3*10**4, 2.7*10**4, 3*10**4]

P980_values1215 = [4.4*10**3, 5*10**3, 6*10**3, 7.5*10**3, 9.1*10**3, 1.1*10**4, 1.4*10**4, 1.7*10**4, 2*10**4, 2.3*10**4, 2.7*10**4, 3*10**4]

P980_values50 = [1.2*10**3, 1.8*10**3, 2.8*10**3, 4.4*10**3, 7.5*10**3, 1.1*10**4, 1.4*10**4, 1.7*10**4, 2*10**4, 2.3*10**4, 2.7*10**4, 3*10**4]



blue4 = [2*10, 1.1*10**2, 8*10**2, 1.6*10**3, 2*10**3, 2.2*10**3, 2.8*10**3, 3*10**3, 3*10**3, 3.5*10**3, 3.6*10**3, 4*10**3, 4.2*10**3, 4.3*10**3, 4.4*10**3]
blue6 = [2, 1.4*10, 1.1*10**2, 1.2*10**3, 1.5*10**3, 2*10**3, 2.5*10**3, 3*10**3, 3.4*10**3, 4*10**3, 4.5*10**3, 5*10**3, 5.4*10**3, 5.5*10**3, 5.6*10**3]
blue8 = [5, 3*10, 6*10**2, 8*10**2, 1.1*10**3, 1.6*10**3, 2.2*10**3, 2.5*10**3, 3*10**3, 3.5*10**3, 4*10**3, 4.5*10**3, 5*10**3, 5.5*10**3]
blue10 = [4.5, 4.5*10, 1.1*10**2, 2.4*10**2, 5.5*10**2, 8.5*10**2, 1.1*10**3, 1.5*10**3, 2*10**3, 2.4*10**3, 2.6*10**3, 3.2*10**3, 3.5*10**3]
blue12 = [1.2*10, 2.8*10, 4*10, 1.2*10**2, 2.2*10**2, 2*10**2, 6.5*10**2, 8*10**2, 1.4*10**3, 1.5*10**3, 1.6*10**3, 2*10**3]
blue15 = [3, 7.5, 2.5*10, 9*10, 2.3*10**2, 2.5*10**2, 5.4*10**2, 7.5*10**2, 9*10**2, 1*10**3, 1.2*10**3, 1.4*10**3]

blue_6_values = [blue4, blue6, blue8, blue10, blue12, blue15]
P980_6_blue = [P980_values, P980_values, P980_values8, P980_values10, P980_values1215, P980_values1215]


NIR4 = [1.2*10**3, 1.6*10**3, 2.7*10**3, 3*10**3, 3.2*10**3, 3.5*10**3, 3.8*10**3, 4*10**3, 3.7*10**3, 3.7*10**3, 3.9*10**3, 4*10**3, 4*10**3, 4*10**3, 4*10**3]
NIR6 = [5.8*10**2, 1.2*10**3, 2.1*10**3, 4.5*10**3, 5*10**3, 5.5*10**3, 6*10**3, 7*10**3, 6.9*10**3, 7*10**3, 7*10**3, 7.1*10**3, 7*10**3, 7*10**3, 7*10**3]
NIR8 = [2.5*10**2, 5.5*10**2, 1.2*10**3, 2.5*10**3, 3*10**3, 3.4*10**3, 3.6*10**3, 4.4*10**3, 4.8*10**3, 5*10**3, 5.1*10**3, 5.5*10**3, 6*10**3, 6.5*10**3, 7*10**3]
NIR10 = [1.1*10**2, 2.5*10**2, 7*10**2, 1.8*10**3, 2.4*10**3, 2.8*10**3, 3.8*10**3, 4.5*10**3, 5*10**3, 5.1*10**3, 5.2*10**3, 5.5*10**3, 6*10**3, 6.5*10**3, 7*10**3]
NIR12 = [4*10, 1*10**2, 1.8*10**2, 6*10**2, 8*10**2, 1.4*10**3, 1.9*10**3, 2.5*10**3, 3*10**3, 4*10**3, 4.5*10**3, 4.5*10**3, 4.1*10**3, 4.2*10**3, 4.2*10**3]
NIR15 = [3*10, 6*10, 1.4*10**2, 6*10**2, 8*10**2, 1.4*10**3, 2*10**3, 2.6*10**3, 3.5*10**3, 4*10**3, 4.5*10**3, 4.9*10**3, 5*10**3, 5*10**3, 5*10**3]
NIR50 = [3, 6.5, 10, 2.4*10, 5.5*10, 1*10**2, 1.4*10**2, 1.5*10**2, 2.5*10**2, 3.1*10**2, 4.2*10**2, 5.2*10**2]

NIR_7_values = [NIR4, NIR6, NIR8, NIR10, NIR12, NIR15, NIR50]
P980_7_NIR = [P980_values, P980_values, P980_values, P980_values, P980_values, P980_values, P980_values50]



blue_std4 = []
blue_std6 = []
blue_std8 = []
blue_std10 = []
blue_std12 = []
blue_std15 =[]
blue_std = [blue_std4, blue_std6, blue_std8, blue_std10, blue_std12, blue_std15]


NIR_std4 = []
NIR_std6 = []
NIR_std8 = []
NIR_std10 = []
NIR_std12 = []
NIR_std15 =[]
NIR_std50 =[]
NIR_std = [NIR_std4, NIR_std6, NIR_std8, NIR_std10, NIR_std12, NIR_std15, NIR_std50]



In [11]:

Cr = 8 / 100  # 8%


def calculate_up(up, C2):
    C2 = C2 / 100
    return 3 * up / (2 + (Cr / C2) ** 2)

    # update cross-relaxation

def calculate_k(k, C2):
    C2 = C2 / 100
    return k * (C2 / Cr) ** 2


def compute_blue_for_x(x, P980, c1, c2, c3, c4, k31, k41, k51):

    # Compute initial condition
    y = 37 * x
    state0 = [0, y, 0, 0, 0, 0]
    t = np.arange(0.0, 0.001, 0.000001)
    state = odeint(system, state0, t, args=(x, P980, c1, c2, c3, c4, k31, k41, k51))
    blue_total = a41 * W4 * state[:, 4][-1] + a52 * W5 * state[:, 5][-1]

    return blue_total

def compute_NIR_for_x(x, P980, c1, c2, c3, c4, k31, k41, k51):

    # Compute initial condition
    y = 37 * x
    state0 = [0, y, 0, 0, 0, 0]
    t = np.arange(0.0, 0.001, 0.000001)
    state = odeint(system, state0, t, args=(x, P980, c1, c2, c3, c4, k31, k41, k51))
    NIR = a31 * W3 * state[:, 3][-1]

    return NIR


def objective(exponents):

    # c1, c2, c3, c4, k31, k41, k51 = params
    c1_exp, c2_exp, c3_exp, c4_exp, k31_exp, k41_exp, k51_exp = exponents

    # Converting exponent values to actual values
    c1, c2, c3, c4, k31, k41, k51 = (10**c1_exp, 10**c2_exp, 10**c3_exp,
                                 10**c4_exp, 10**k31_exp, 10**k41_exp, 10**k51_exp)

    up_values = [c1, c2, c3, c4]
    k_values = [k31, k41, k51]

    # Tm concentration from 4%, 6%, 8%, 10%, 12%, 15%, 50%, update cross relaxation and new up-conversion values

    C2_range = [4, 6, 8, 10, 12, 15, 50]
    nested_up_list = []
    nested_k_list = []

    for C2 in C2_range:

        up_sublist = [calculate_up(up, C2) for up in up_values]

        k_sublist = [calculate_k(k, C2) for k in k_values]

        nested_up_list.append(up_sublist)

        nested_k_list.append(k_sublist)


    total_error = 0

    x_6_blue = [4, 6, 8, 10, 12, 15]
    x_7_NIR = [4, 6, 8, 10, 12, 15, 50]


    for index, x in enumerate(tqdm(x_6_blue)):

        # parameters are fixed at the given concentration
        c1, c2, c3, c4 = nested_up_list[index]
        k31, k41, k51 = nested_k_list[index]

        # different power density at each concentration
        for P980, blue_exp in tqdm(zip(P980_6_blue[index], blue_6_values[index])):

            # call ODE
            blue_cal = compute_blue_for_x(x, P980, c1, c2, c3, c4, k31, k41, k51)

            error_blue = ((blue_cal - blue_exp)/blue_exp)**2

            total_error += error_blue


    for index, x in enumerate(tqdm(x_7_NIR)):

        # parameters are fixed at the given concentration
        c1, c2, c3, c4 = nested_up_list[index]
        k31, k41, k51 = nested_k_list[index]

        # different power density at each concentration
        for P980, NIR_exp in tqdm(zip(P980_7_NIR[index], NIR_7_values[index])):

            # call ODE
            NIR_cal = compute_NIR_for_x(x, P980, c1, c2, c3, c4, k31, k41, k51)

            error_NIR = ((NIR_cal - NIR_exp)/NIR_exp)**2

            total_error += error_NIR

    return total_error, # a return statement with a trailing comma, it means the function is returning a tuple with a single element.



In [12]:
import time

start_time = time.time()

alpha1 = 0.1
Average = 0
Std = 3
Mut_p = 0.2
POP_SIZE = 100
CXPB = 0.7
MUTPB = 0.2
NGEN = 60
Cr = 8 / 100

# aim to minimize its values
creator.create("FitnessMin", base.Fitness, weights=(-1.0,))

creator.create("Individual", list, fitness=creator.FitnessMin)

# The toolbox is a container for various functions used in the genetic algorithm
toolbox = base.Toolbox()

# valid_values = [10**i for i in range(-20, 20)]
# toolbox.register("attr_float", random.choice, valid_values) # discrete

valid_values = [i for i in range(-10, 10)]
toolbox.register("attr_float", random.choice, valid_values)


toolbox.register("individual", tools.initRepeat, creator.Individual, toolbox.attr_float, n=7)

toolbox.register("population", tools.initRepeat, list, toolbox.individual) # create a list of individuals, essentially generating the initial population

# Genetic Operators
toolbox.register("mate", tools.cxBlend, alpha= alpha1)

toolbox.register("mutate", tools.mutGaussian, mu=Average, sigma=Std, indpb=Mut_p)

# Evaluation Function
toolbox.register("evaluate", objective)

toolbox.register("select", tools.selTournament, tournsize=3)

pop = toolbox.population(n=POP_SIZE)

fits = list(map(toolbox.evaluate, pop))

for fit, ind in zip(fits, pop):
    ind.fitness.values = fit

for gen in range(NGEN):
    offspring = algorithms.varAnd(pop, toolbox, CXPB, MUTPB)
    # fits = list(map(toolbox.evaluate, offspring))
    for ind in offspring:
        fit = toolbox.evaluate(ind)
        ind.fitness.values = fit

    pop = toolbox.select(offspring, k=len(pop))

top10 = tools.selBest(pop, k=10)

end_time = time.time()

elapsed_time = end_time - start_time

print(f"Elapsed time: {elapsed_time} seconds")

  0%|                                                     | 0/6 [00:00<?, ?it/s]
0it [00:00, ?it/s]/Users/jayliu/anaconda3/lib/python3.11/site-packages/scipy/integrate/_odepack_py.py:248: ODEintWarning: Excess work done on this call (perhaps wrong Dfun type). Run with full_output = 1 to get quantitative information.
  warnings.warn(warning_msg, ODEintWarning)

15it [00:00, 106.14it/s]
 17%|███████▌                                     | 1/6 [00:00<00:00,  6.99it/s]
0it [00:00, ?it/s]
15it [00:00, 130.67it/s]
 33%|███████████████                              | 2/6 [00:00<00:00,  7.77it/s]
0it [00:00, ?it/s]
14it [00:00, 133.68it/s]
 50%|██████████████████████▌                      | 3/6 [00:00<00:00,  8.42it/s]
13it [00:00, 147.43it/s]

12it [00:00, 148.78it/s]
 83%|█████████████████████████████████████▌       | 5/6 [00:00<00:00,  9.95it/s]
12it [00:00, 146.90it/s]
  0%|                                                     | 0/7 [00:00<?, ?it/s]
0it [00:00, ?it/s]
15it [00:00, 108.03it/s]

 lsoda--  at t (=r1) and step size h (=r2), the      
       corrector convergence failed repeatedly       
       or with abs(h) = hmin     
      in above,  r1 =  0.1108969877381D-07   r2 =  0.4228338437047D-13


  0%|                                                     | 0/6 [00:00<?, ?it/s]
15it [00:00, 271.59it/s]

15it [00:00, 248.97it/s]
 33%|███████████████                              | 2/6 [00:00<00:00, 17.01it/s]
14it [00:00, 230.43it/s]

13it [00:00, 219.52it/s]
 67%|██████████████████████████████               | 4/6 [00:00<00:00, 16.49it/s]
12it [00:00, 229.25it/s]

12it [00:00, 237.26it/s]
  0%|                                                     | 0/7 [00:00<?, ?it/s]
15it [00:00, 260.96it/s]

15it [00:00, 244.25it/s]
 29%|████████████▊                                | 2/7 [00:00<00:00, 16.53it/s]
15it [00:00, 233.29it/s]

15it [00:00, 249.82it/s]
 57%|█████████████████████████▋                   | 4/7 [00:00<00:00, 15.96it/s]
15it [00:00, 239.26it/s]

15it [00:00, 260.38it/s]
 86%|██████████████████████████████████████▌      | 6/7 [00:00<00:00, 15.92it/s]
12it [00:00, 349.50it/s]
  0%|                                                     | 0/6 [00:00<?, ?it/s]
0it [00:00, ?it/s]
15

 lsoda--  at t (=r1) and step size h (=r2), the      
       corrector convergence failed repeatedly       
       or with abs(h) = hmin     
      in above,  r1 =  0.5823499598318D-07   r2 =  0.1110281607821D-12


  0%|                                                     | 0/6 [00:00<?, ?it/s]
15it [00:00, 197.59it/s]

0it [00:00, ?it/s]
15it [00:00, 112.36it/s]
 33%|███████████████                              | 2/6 [00:00<00:00,  9.22it/s]
0it [00:00, ?it/s]
14it [00:00, 100.25it/s]A
 50%|██████████████████████▌                      | 3/6 [00:00<00:00,  7.84it/s]
13it [00:00, 151.33it/s]

12it [00:00, 190.37it/s]
 83%|█████████████████████████████████████▌       | 5/6 [00:00<00:00, 10.02it/s]
12it [00:00, 181.96it/s]
  0%|                                                     | 0/7 [00:00<?, ?it/s]
15it [00:00, 196.38it/s]

15it [00:00, 177.45it/s]
 29%|████████████▊                                | 2/7 [00:00<00:00, 12.22it/s]
15it [00:00, 192.24it/s]

15it [00:00, 164.42it/s]
 57%|█████████████████████████▋                   | 4/7 [00:00<00:00, 11.88it/s]
15it [00:00, 177.30it/s]

15it [00:00, 195.70it/s]
 86%|██████████████████████████████████████▌      | 6/7 [00:00<00:00, 12.00it/s]
12it [00

...

 lsoda--  at t (=r1) and step size h (=r2), the      
       corrector convergence failed repeatedly       
       or with abs(h) = hmin     
      in above,  r1 =  0.5823499598318D-07   r2 =  0.1110281607821D-12


  0%|                                                     | 0/6 [00:00<?, ?it/s]
15it [00:00, 239.95it/s]

15it [00:00, 255.46it/s]
 33%|███████████████                              | 2/6 [00:00<00:00, 15.73it/s]
14it [00:00, 264.84it/s]

13it [00:00, 211.76it/s]
 67%|██████████████████████████████               | 4/6 [00:00<00:00, 16.30it/s]
12it [00:00, 234.56it/s]

12it [00:00, 237.16it/s]
  0%|                                                     | 0/7 [00:00<?, ?it/s]
15it [00:00, 252.06it/s]

15it [00:00, 272.24it/s]
 29%|████████████▊                                | 2/7 [00:00<00:00, 16.67it/s]
15it [00:00, 255.58it/s]

15it [00:00, 250.70it/s]
 57%|█████████████████████████▋                   | 4/7 [00:00<00:00, 15.69it/s]
15it [00:00, 242.27it/s]

15it [00:00, 260.95it/s]
 86%|██████████████████████████████████████▌      | 6/7 [00:00<00:00, 15.94it/s]
12it [00:00, 346.15it/s]
  0%|                                                     | 0/6 [00:00<?, ?it/s]
15it [00:00, 268.38it

 lsoda--  at t (=r1) and step size h (=r2), the      
       corrector convergence failed repeatedly       
       or with abs(h) = hmin     
      in above,  r1 =  0.1563195812317D-06   r2 =  0.3924594858092D-12


  0%|                                                     | 0/6 [00:00<?, ?it/s]
15it [00:00, 756.08it/s]

15it [00:00, 724.01it/s]

14it [00:00, 813.10it/s]

13it [00:00, 843.99it/s]

12it [00:00, 857.13it/s]

12it [00:00, 723.89it/s]
  0%|                                                     | 0/7 [00:00<?, ?it/s]
15it [00:00, 754.30it/s]

15it [00:00, 776.07it/s]

15it [00:00, 875.56it/s]

15it [00:00, 883.18it/s]

15it [00:00, 791.69it/s]

15it [00:00, 695.38it/s]
 86%|██████████████████████████████████████▌      | 6/7 [00:00<00:00, 48.88it/s]
12it [00:00, 229.85it/s]
  0%|                                                     | 0/6 [00:00<?, ?it/s]
15it [00:00, 660.68it/s]

15it [00:00, 827.49it/s]

14it [00:00, 846.96it/s]

13it [00:00, 865.00it/s]

12it [00:00, 805.68it/s]

12it [00:00, 761.32it/s]
  0%|                                                     | 0/7 [00:00<?, ?it/s]
15it [00:00, 879.87it/s]

15it [00:00, 594.20it/s]

15it [00:00, 569.37it/s]

15it [00:00, 797.15it/s]

1

Elapsed time: 3174.263242959976 seconds


In [13]:
top10

[[2.5511755767196287,
  -1.559050301735759,
  0.568694474571075,
  -3.4641205569144824,
  -0.40244010017899023,
  0.4894985080564554,
  -4.252266420490009],
 [2.5511755767196287,
  -1.559050301735759,
  0.568694474571075,
  -3.4641205569144824,
  -0.40244010017899023,
  0.4894985080564554,
  -4.252266420490009],
 [2.5511755767196287,
  -1.559050301735759,
  0.568694474571075,
  -3.4641205569144824,
  -0.40244010017899023,
  0.4894985080564554,
  -4.252266420490009],
 [2.5511755767196287,
  -1.559050301735759,
  0.568694474571075,
  -3.4641205569144824,
  -0.40244010017899023,
  0.4894985080564554,
  -4.252266420490009],
 [2.551690875716354,
  -1.559040063368324,
  0.568688723012335,
  -3.0256113628886294,
  -0.40417117177966394,
  0.40243375307016827,
  -6.720215877105998],
 [2.551690875716354,
  -1.559040063368324,
  0.568688723012335,
  -3.0256113628886294,
  -0.40417117177966394,
  0.40243375307016827,
  -6.720215877105998],
 [2.551690875716354,
  -1.559040063368324,
  0.56868872301

# Parameters box plot

In [ ]:
import plotly.graph_objects as go
from IPython.core.display import display, HTML

# Extract the top ten individuals from each run (there are totally NUM_RUNS=10 runs)



for i in range(1):

    top_ten_individuals = top10

    # Unzipping the parameters
    c1_exps, c2_exps, c3_exps, c4_exps, k31_exps, k41_exps, k51_exps = zip(*top_ten_individuals)

    # Create subplots
    fig = go.Figure()

    # Adding subplots for each parameter
    params = [c1_exps, c2_exps, c3_exps, c4_exps, k31_exps, k41_exps, k51_exps]
    param_names = ["c1_exp", "c2_exp", "c3_exp", "c4_exp", "k31_exp", "k41_exp", "k51_exp"]

    for param, name in zip(params, param_names):
        fig.add_trace(go.Box(
            y=param,
            name=name
        ))


    fig.update_xaxes(showgrid=True, gridwidth=2, gridcolor='white')
    fig.update_yaxes(showgrid=True, gridwidth=2, gridcolor='white')

    fig.update_layout(
                title=f"Parameter exponents of top ten individuals",
                title_font=dict(size=24, family="Courier New, monospace"),
                title_x=0.5,  # center
                title_y=0.9,
                width=800, height=700,
                yaxis_title="Parameter Exponent Value",
                xaxis_title="Seven Parameter Exponents",
                xaxis=dict(
                title_font=dict(size=22, family="Courier New, monospace"),
                tickfont=dict(size=22, family="Courier New, monospace")
            ),
            yaxis=dict(
                title_font=dict(size=22, family="Courier New, monospace"),
                tickfont=dict(size=22, family="Courier New, monospace")
            )
            )


    fig.show()

# UCL v.s. Power density

In [ ]:
import numpy as np
from scipy.integrate import odeint
from tqdm import tqdm
import time
import random

# Constants
a21 = 1
a31 = 0.27
a32 = 0.73

a41 = 0.18
a42 = 0.24
a43 = 0.58

a51 = 0.24
a52 = 0.23
a53 = 0.2
a54 = 0.33

W2 = 63000
W3 = 20000
W4 = 15000
W5 = 33000
Ws2 = 8000


def system(state, t, x, P980, c1, c2, c3, c4, k31, k41, k51):

    ns2, n1, n2, n3, n4, n5 = state

    #ns2
    ms2 = 1.23*P980*(37*(100-x)-ns2) - Ws2*ns2 - (c1*n1+c2*n2+c3*n3+c4*n4)*ns2  # ns1 = total_Yb - ns2

    # n1
    m1 = -c1*n1*ns2 + a21*W2*n2 + a31*W3*n3 + a41*W4*n4 + a51*W5*n5 - k41*n1*n4 - k31*n1*n3 - k51*n5*n1

    # n2
    m2 = c1*n1*ns2 - c2*n2*ns2 - a21*W2*n2 + a32*W3*n3 + a42*W4*n4 + a52*W5*n5 + k41*n1*n4 + 2*k31*n1*n3

    # n3
    m3 = c2*n2*ns2 - c3*n3*ns2 - (a31+a32)*W3*n3 + a43*W4*n4 + a53*W5*n5 + 2*k51*n1*n5 + k41*n1*n4 - k31*n1*n3

    # n4
    m4 = c3*n3*ns2 - c4*n4*ns2 - (a43+a42+a41)*W4*n4 + a54*W5*n5 - k41*n1*n4

    # n5
    m5 = c4*n4*ns2 - (a54+a53+a52+a51)*W5*n5 - k51*n1*n5


    return [ms2, m1, m2, m3, m4, m5]

In [ ]:

# Time array
t = np.arange(0.0, 0.001, 0.000001)

x_values = [4, 6, 8, 10, 12, 15, 50]


P980_values = np.arange(10**3, 10**5, 2000)


n3_NIR=[[] for i in range(7)]

n4_n5_blue=[[] for i in range(7)]




for index, x in enumerate(tqdm(x_values)):

    c1, c2, c3, c4 = nested_up_list[index]

    k31, k41, k51 = nested_k_list[index]

    y = 37 * x
    state0 = [0, y, 0, 0, 0, 0]

    for P980 in tqdm(P980_values):



        state = odeint(system, state0, t, args=(x, P980, c1, c2, c3, c4, k31, k41, k51))

        # NIR

        n3_NIR[index].append(a31*W3*state[:, 3][-1])

        # blue

        n4_n5_blue[index].append(a41*W4*state[:, 4][-1] + a52*W5*state[:, 5][-1])




# NIR emission (UCL v.s. Power density)

In [ ]:
from IPython.core.display import display, HTML


P980_values = [1.2*10**3, 1.8*10**3, 2.8*10**3, 4.4*10**3, 5*10**3, 6*10**3, 7.5*10**3, 9.1*10**3, 1.1*10**4, 1.4*10**4, 1.7*10**4, 2*10**4, 2.3*10**4, 2.7*10**4, 3*10**4]

P980_values8 = [1.8*10**3, 2.8*10**3, 4.4*10**3, 5*10**3, 6*10**3, 7.5*10**3, 9.1*10**3, 1.1*10**4, 1.4*10**4, 1.7*10**4, 2*10**4, 2.3*10**4, 2.7*10**4, 3*10**4]

P980_values10 = [2.8*10**3, 4.4*10**3, 5*10**3, 6*10**3, 7.5*10**3, 9.1*10**3, 1.1*10**4, 1.4*10**4, 1.7*10**4, 2*10**4, 2.3*10**4, 2.7*10**4, 3*10**4]

P980_values1215 = [4.4*10**3, 5*10**3, 6*10**3, 7.5*10**3, 9.1*10**3, 1.1*10**4, 1.4*10**4, 1.7*10**4, 2*10**4, 2.3*10**4, 2.7*10**4, 3*10**4]

P980_values50 = [1.2*10**3, 1.8*10**3, 2.8*10**3, 4.4*10**3, 7.5*10**3, 1.1*10**4, 1.4*10**4, 1.7*10**4, 2*10**4, 2.3*10**4, 2.7*10**4, 3*10**4]


blue4 = [2*10, 1.1*10**2, 8*10**2, 1.6*10**3, 2*10**3, 2.2*10**3, 2.8*10**3, 3*10**3, 3*10**3, 3.5*10**3, 3.6*10**3, 4*10**3, 4.2*10**3, 4.3*10**3, 4.4*10**3]
blue6 = [2, 1.4*10, 1.1*10**2, 1.2*10**3, 1.5*10**3, 2*10**3, 2.5*10**3, 3*10**3, 3.4*10**3, 4*10**3, 4.5*10**3, 5*10**3, 5.4*10**3, 5.5*10**3, 5.6*10**3]
blue8 = [5, 3*10, 6*10**2, 8*10**2, 1.1*10**3, 1.6*10**3, 2.2*10**3, 2.5*10**3, 3*10**3, 3.5*10**3, 4*10**3, 4.5*10**3, 5*10**3, 5.5*10**3]
blue10 = [4.5, 4.5*10, 1.1*10**2, 2.4*10**2, 5.5*10**2, 8.5*10**2, 1.1*10**3, 1.5*10**3, 2*10**3, 2.4*10**3, 2.6*10**3, 3.2*10**3, 3.5*10**3]
blue12 = [1.2*10, 2.8*10, 4*10, 1.2*10**2, 2.2*10**2, 2*10**2, 6.5*10**2, 8*10**2, 1.4*10**3, 1.5*10**3, 1.6*10**3, 2*10**3]
blue15 = [3, 7.5, 2.5*10, 9*10, 2.3*10**2, 2.5*10**2, 5.4*10**2, 7.5*10**2, 9*10**2, 1*10**3, 1.2*10**3, 1.4*10**3]

NIR4 = [1.2*10**3, 1.6*10**3, 2.7*10**3, 3*10**3, 3.2*10**3, 3.5*10**3, 3.8*10**3, 4*10**3, 3.7*10**3, 3.7*10**3, 3.9*10**3, 4*10**3, 4*10**3, 4*10**3, 4*10**3]
NIR6 = [5.8*10**2, 1.2*10**3, 2.1*10**3, 4.5*10**3, 5*10**3, 5.5*10**3, 6*10**3, 7*10**3, 6.9*10**3, 7*10**3, 7*10**3, 7.1*10**3, 7*10**3, 7*10**3, 7*10**3]
NIR8 = [2.5*10**2, 5.5*10**2, 1.2*10**3, 2.5*10**3, 3*10**3, 3.4*10**3, 3.6*10**3, 4.4*10**3, 4.8*10**3, 5*10**3, 5.1*10**3, 5.5*10**3, 6*10**3, 6.5*10**3, 7*10**3]
NIR10 = [1.1*10**2, 2.5*10**2, 7*10**2, 1.8*10**3, 2.4*10**3, 2.8*10**3, 3.8*10**3, 4.5*10**3, 5*10**3, 5.1*10**3, 5.2*10**3, 5.5*10**3, 6*10**3, 6.5*10**3, 7*10**3]
NIR12 = [4*10, 1*10**2, 1.8*10**2, 6*10**2, 8*10**2, 1.4*10**3, 1.9*10**3, 2.5*10**3, 3*10**3, 4*10**3, 4.5*10**3, 4.5*10**3, 4.1*10**3, 4.2*10**3, 4.2*10**3]
NIR15 = [3*10, 6*10, 1.4*10**2, 6*10**2, 8*10**2, 1.4*10**3, 2*10**3, 2.6*10**3, 3.5*10**3, 4*10**3, 4.5*10**3, 4.9*10**3, 5*10**3, 5*10**3, 5*10**3]
NIR50 = [3, 6.5, 10, 2.4*10, 5.5*10, 1*10**2, 1.4*10**2, 1.5*10**2, 2.5*10**2, 3.1*10**2, 4.2*10**2, 5.2*10**2]



"red", "green", "blue", "goldenrod", "magenta"




fig3 = go.Figure()

fig3.add_trace(go.Scatter(x=P980_values, y=n3_NIR[0], mode='lines', name='4% Tm', marker=dict(color='red')))

fig3.add_trace(go.Scatter(x=P980_values, y=n3_NIR[1], mode='lines', name='6% Tm', marker=dict(color='green')))

fig3.add_trace(go.Scatter(x=P980_values, y=n3_NIR[2], mode='lines', name='8% Tm', marker=dict(color='blue')))

fig3.add_trace(go.Scatter(x=P980_values, y=n3_NIR[3], mode='lines', name='10% Tm',marker=dict(color='goldenrod')))

fig3.add_trace(go.Scatter(x=P980_values, y=n3_NIR[4], mode='lines', name='12% Tm',marker=dict(color='magenta')))

fig3.add_trace(go.Scatter(x=P980_values, y=n3_NIR[5], mode='lines', name='15% Tm',marker=dict(color='#AB63FA')))

fig3.add_trace(go.Scatter(x=P980_values, y=n3_NIR[6], mode='lines', name='50% Tm',marker=dict(color='black')))

fig3.add_trace(go.Scatter(x=P980_values, y = NIR4, mode='markers', name='4% Tm', marker=dict(color='red')))

fig3.add_trace(go.Scatter(x=P980_values, y = NIR6, mode='markers', name='6% Tm', marker=dict(color='green')))

fig3.add_trace(go.Scatter(x=P980_values, y = NIR8, mode='markers', name='8% Tm', marker=dict(color='blue')))

fig3.add_trace(go.Scatter(x=P980_values, y = NIR10, mode='markers', name='10% Tm',marker=dict(color='goldenrod')))

fig3.add_trace(go.Scatter(x=P980_values, y = NIR12, mode='markers', name='12% Tm',marker=dict(color='magenta')))

fig3.add_trace(go.Scatter(x=P980_values, y = NIR15, mode='markers', name='15% Tm',marker=dict(color='#AB63FA')))

fig3.add_trace(go.Scatter(x=P980_values50, y = NIR50, mode='markers', name='50% Tm',marker=dict(color='black')))





fig3.update_xaxes(type="log", title_text='Power density (W/cm^2)', title_font=dict(size=18, color='black'),tickfont=dict(size=18),showgrid=True, gridwidth=2, gridcolor='white')
fig3.update_yaxes(type="log", title_text='Intensity(PPS)',title_font=dict(size=18, color='black'),tickfont=dict(size=18),showgrid=True, gridwidth=2, gridcolor='white')

fig3.update_layout(
    title_text='NIR v.s. Power density (1-x)% Yb, x% Tm',  # Main Title
    title_font=dict(size=24, family="Arial, sans-serif", color='royalblue'),
    width=1200, height=1000,
    title_x=0.5,  # Center the main title
    title_y=0.95,  # Adjust the vertical position of the main title
    showlegend=True, margin=dict(l=20, r=20, b=20, t=70),
    legend=dict(
        font=dict(
            size=20,
            family="Arial, sans-serif"
        )
    )
    )


# blue emission (UCL v.s. Power density)

In [ ]:

fig4 = go.Figure()
fig4.add_trace(go.Scatter(x=P980_values, y=n4_n5_blue[0], mode='lines', name='4% Tm', marker=dict(color='red')))
fig4.add_trace(go.Scatter(x=P980_values, y=n4_n5_blue[1], mode='lines', name='6% Tm', marker=dict(color='green')))
fig4.add_trace(go.Scatter(x=P980_values, y=n4_n5_blue[2], mode='lines', name='8% Tm', marker=dict(color='blue')))
fig4.add_trace(go.Scatter(x=P980_values, y=n4_n5_blue[3], mode='lines', name='10% Tm',marker=dict(color='goldenrod')))
fig4.add_trace(go.Scatter(x=P980_values, y=n4_n5_blue[4], mode='lines', name='12% Tm',marker=dict(color='magenta')))
fig4.add_trace(go.Scatter(x=P980_values, y=n4_n5_blue[5], mode='lines', name='15% Tm',marker=dict(color='black')))

fig4.add_trace(go.Scatter(x=P980_values, y = blue4, mode='markers', name='4% Tm', marker=dict(color='red')))
fig4.add_trace(go.Scatter(x=P980_values, y = blue6, mode='markers', name='6% Tm', marker=dict(color='green')))
fig4.add_trace(go.Scatter(x=P980_values8, y = blue8, mode='markers', name='8% Tm', marker=dict(color='blue')))
fig4.add_trace(go.Scatter(x=P980_values10, y = blue10, mode='markers', name='10% Tm', marker=dict(color='goldenrod')))
fig4.add_trace(go.Scatter(x=P980_values1215, y = blue12, mode='markers', name='12% Tm', marker=dict(color='magenta')))
fig4.add_trace(go.Scatter(x=P980_values1215, y = blue15, mode='markers', name='15% Tm', marker=dict(color='black')))


#fig4.add_trace(go.Scatter(x=P980_values, y=n4_n5_blue[6], mode='lines+markers', name='50% Tm',))


fig4.update_xaxes(type="log", title_text='Power density (W/cm^2)', title_font=dict(size=18, color='black'),tickfont=dict(size=18),showgrid=True, gridwidth=2, gridcolor='white')
fig4.update_yaxes(type="log", title_text='Intensity(PPS)',title_font=dict(size=18, color='black'),tickfont=dict(size=18),showgrid=True, gridwidth=2, gridcolor='white')

fig4.update_layout(
    title_text='Blue v.s. Power density (1-x)% Yb, x% Tm',  # Main Title
    title_font=dict(size=24, family="Arial, sans-serif", color='royalblue'),
    width=1200, height=1000,
    title_x=0.5,  # Center the main title
    title_y=0.95,  # Adjust the vertical position of the main title
    showlegend=True, margin=dict(l=20, r=20, b=20, t=70),
    legend=dict(
        font=dict(
            size=20,
            family="Arial, sans-serif"
        )
    )
    )



